<a href="https://colab.research.google.com/github/graylan0/quantum-machine-learning/blob/main/singing.bark.multi.threaded.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install --pre torch torchvision -f https://download.pytorch.org/whl/nightly/cu102/torch_nightly.html -U
!pip install git+https://github.com/suno-ai/bark.git
!pip install openai
!pip install scipy

Looking in links: https://download.pytorch.org/whl/nightly/cu102/torch_nightly.html
  Cloning https://github.com/suno-ai/bark.git to /tmp/pip-req-build-5h8hgc92
  Running command git clone --filter=blob:none --quiet https://github.com/suno-ai/bark.git /tmp/pip-req-build-5h8hgc92
  Resolved https://github.com/suno-ai/bark.git to commit 42d579ddcd2089be7791ba65f22abd99e0ce63a5
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Installing backend dependencies ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 135.8/135.8 kB 2.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.7/3.7 MB 15.9 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 294.8/294.8 kB 19.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.8/3.8 MB 35.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.6/7.6 MB 60.6 MB/s eta 0:00:00
    

In [11]:
!pip install scipy
!pip install sounddevice
!pip install fastapi uvicorn

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 66.2/66.2 kB 2.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 59.5/59.5 kB 5.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 67.0/67.0 kB 6.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 6.6 MB/s eta 0:00:00


In [10]:
from bark import SAMPLE_RATE, generate_audio, preload_models
from scipy.io.wavfile import write as write_wav
from IPython.display import Audio
from concurrent.futures import ThreadPoolExecutor
import numpy as np
import uuid
import os

# Preload models
preload_models()

os.environ["SUNO_USE_SMALL_MODELS"] = "True"

def generate_audio_for_sentence(sentence):
    return generate_audio(sentence)

def generate_response(song_elements, num_threads=4):
    pieces = []

    with ThreadPoolExecutor(max_workers=num_threads) as executor:
        future_to_element = {executor.submit(generate_audio_for_sentence, element.get('lyrics', element.get('music'))): element for element in song_elements if 'lyrics' in element or 'music' in element}

        for future in future_to_element:
            audio_array = future.result()
            pieces += [audio_array]

            element = future_to_element[future]
            if 'pause' in element:
                silence = np.zeros(int(element['pause'] * SAMPLE_RATE))
                pieces += [silence]

    audio = np.concatenate(pieces)
    file_name = str(uuid.uuid4()) + ".wav"
    write_wav(file_name, SAMPLE_RATE, audio.astype(np.int16))
    print(f"Audio generation completed and saved to {file_name}")
    return Audio(audio, rate=SAMPLE_RATE)

song_elements = [
    {'music': "Soft ukulele strums, tempo 120", 'pause': 2},
    {'lyrics': "Love on the island, sun in the sky, feeling so high", 'pause': 1},
    {'lyrics': "The breeze whispers secrets, as we let the time fly", 'pause': 2},
    {'lyrics': "Dance, dance, under the moonlight, let's make this a beautiful night", 'pause': 1},
    {'music': "musich", 'pause': 1},
    {'lyrics': "Waves are crashing, hearts are smashing, yet we're so free", 'pause': 2},
    {'lyrics': "The stars are our spotlight, as we carve our love on a palm tree", 'pause': 1},
    {'music': "music", 'pause': 1},
    {'lyrics': "But we're still here, love's so clear, like the ocean so deep", 'pause': 2},
    {'lyrics': "Dance, dance, under the moonlight, let's make memories to keep", 'pause': 1},
    {'lyrics': "And so we say Aloha, as the sun greets the dawn", 'pause': 2},
    {'end': "Soft ukulele fade-out, tempo slows to 90"}
]

audio_output = generate_response(song_elements)
audio_output  # This should play the audio in the notebook



100%|██████████| 36/36 [00:32<00:00,  1.11it/s]


Audio generation completed and saved to ebcb0429-9e40-4d82-a279-4bf3026a5139.wav
